In [ ]:
import numpy as np
import time
import matplotlib.pyplot as plt 
from mpl_toolkits.mplot3d import Axes3D
from io import BytesIO
from PIL import Image
import cv2
import glob, os

import sys
sys.path.insert(0, '/home/till/code/4/driving/experimental/till/depth_error_simulation/')
from func_util import *

datapath = "/tmp/12/"
outpath = "/tmp/123v/"
wh = np.array([1920.0,1200.0])

In [ ]:
os.chdir(datapath)
p_fl = glob.glob("*.txt")
noiter = len(p_fl)
camextr = [None] * noiter
camintr = [None] * noiter
for i in xrange(noiter):
    lines = [np.fromstring(line.rstrip('\n'), dtype=float, sep=',') for line in open(datapath + '_pose_{:04}.txt'.format(i))]
    camextr[i] = lines[0::2]
    camintr[i] = lines[1::2]
    #print lines
for i in xrange(noiter):
    for j in xrange(len(camextr[i])):
        camextr[i][j] = np.array(camextr[i][j]).reshape(4,4).T

In [ ]:
def func_invert_transform(Pin):
    P = Pin.copy()
    P[0:3,0:3] = P[0:3,0:3].T # R.T
    P[0:3,3] = np.dot(-P[0:3,0:3], P[0:3,3]) # -R.T * t
    return P

def func_P_to_Rt(P):
    return P[0:3,0:3], P[0:3,3]

In [ ]:
# Create one frame for each iteration

for fr in xrange(0,noiter,1):
    fig = plt.figure(figsize=(30,24))
    ax = fig.add_subplot(111, projection='3d')
    cammean = np.array([0.0,0.0,0.0])
    for cnt in xrange(len(camextr[fr])):
        # plot final camera
        camcol = np.array([0.5, 0.5, 0.5])
        cc = camintr[noiter-1][cnt][[2,3]] - wh/2        
        R,t = func_P_to_Rt(camextr[noiter-1][cnt])
        cammean += t
        func_plot_cameras(ax, camintr[noiter-1][cnt][[0,1]], cc, wh, R, t, rgbface=camcol, camerascaling=1)
        ax.scatter(0, 0, 0, color=camcol, linewidth=0.01)
        ax.scatter(t[0], t[1], t[2], color=camcol, linewidth=0.01)
        
    func_set_axes_equal(ax)        
    xlm=ax.get_xlim3d()
    ylm=ax.get_ylim3d()
    zlm=ax.get_zlim3d()
    
    for cnt in xrange(len(camextr[fr])):    
        # plot new camera        
        camcol = np.array([1.0, 0.0, 0.0])
        if (camintr[fr][cnt][0] > 2000): 
            camcol = np.array([0.0, 0.0, 1.0])
        cc = camintr[fr][cnt][[2,3]] - wh/2        
        R,t = func_P_to_Rt(camextr[fr][cnt])
        func_plot_cameras(ax, camintr[fr][cnt][[0,1]], cc, wh, R, t, rgbface=camcol, camerascaling=1)
        ax.scatter(0, 0, 0, color=camcol, linewidth=0.5)
        ax.scatter(t[0], t[1], t[2], color=camcol, linewidth=0.5)
        
    #func_set_axes_equal(ax)
    ax.view_init(elev=45., azim=115)

    func_set_axes_equal(ax)
    ax.set_xlim3d(xlm)
    ax.set_ylim3d(ylm)
    ax.set_zlim3d(zlm)
    
    ax.set_xlabel('x')
    ax.set_ylabel('y')
    ax.set_zlabel('z')
    plt.show()
    
    savefile =  outpath + "vis_plot_pose_{:06d}.png".format(fr)
    fig.savefig(savefile, format='png')

In [ ]:
# Create 4x4 image with Top row: Fmat matches left and right, Bottom row: Lidar reprojection, Full rig.
for fr in xrange(110,noiter,1):
    print fr
    imgout = np.zeros((2*wh[1].astype(int), 2*wh[0].astype(int),3), np.uint8)

    imga = cv2.imread(datapath + "_FmatPair_north_wide_left-north_narrow_left-1518560311.03639-{:04d}.jpg".format(fr))
    imgout[0:wh[1].astype(int),:,:] = imga.copy()
    
    ldfile = datapath + "_lidarImage_west_wide_right-1518560929.30153-{:04d}.jpg".format(fr)
    if (os.path.isfile(ldfile)):
        imgb = cv2.imread(ldfile)
        imgout[wh[1].astype(int):,0:wh[0].astype(int),:] = imgb
        
    imgc = cv2.imread(outpath + "vis_plot_pose_{:06d}.png".format(fr))
    ycent = (imgc.shape[0]-wh[1].astype(int))/2
    xcent = (imgc.shape[1]-wh[0].astype(int))/2
    imgc = imgc[ycent:ycent+wh[1].astype(int), xcent:xcent+wh[0].astype(int),:]
    imgout[wh[1].astype(int):,wh[0].astype(int):,:] = imgc 

    
    cv2.imwrite(outpath + "visimg_plot_all_{:04d}.png".format(fr), imgout)
    
    


    

In [ ]:
# camera plot test
camfile = open('/home/till/Downloads/tett.txt','r')
lines = camfile.read().split('\n')
nocams = len(lines)/2
camextr = lines[1:(2*nocams):2]
print camextr
camextr = [np.fromstring(x, sep=" ").reshape((4,4)) for x in camextr]
camnames = lines[0:(2*nocams):2]

fig = plt.figure(figsize=(30,24))
ax = fig.add_subplot(111, projection='3d')
    
camcol = np.array([1, 0.0, 0.0])
cc = np.array([0,0])
fc = np.array([2500, 2500])
for cnt in xrange(len(camextr)):
    R,t = func_P_to_Rt(camextr[cnt])
    func_plot_cameras(ax, fc, cc, wh, R, t, rgbface=camcol, camerascaling=1.5)
    ax.text(t[0], t[1], t[2], camnames[cnt], color='black')

ax.scatter(0, 0, 0, color=camcol, linewidth=0.01)
ax.view_init(elev=70., azim=115)
func_set_axes_equal(ax)        
xlm=ax.get_xlim3d()
ylm=ax.get_ylim3d()
zlm=ax.get_zlim3d()
ax.set_xlabel('x')
ax.set_ylabel('y')
ax.set_zlabel('z')
    
#lines = [np.fromstring(line.rstrip('\n'), dtype=float, sep=',') for line in open(datapath + '_pose_{:04}.txt'.format(i))]